# Importing

In [1]:
from utilities.Functionnalities import *
import warnings
warnings.filterwarnings("ignore")

# Entries

In [2]:
dateObservation = 24
nbPool = 6
star_time = "2021-07-07"
hour = "00:00:00"
ending_time = "2022-01-01"

# Download Node Modules for nodeJs
### npm install ccxt
### npm install csv-writer

In [3]:
install_package_if_needed("ccxt")
install_package_if_needed("csv-writer")

ccxt is already installed.
csv-writer is already installed.


# 1] Data Collection

### Les Variables

In [3]:
data = {'current_date': pd.to_datetime(['2020-01-02']),
        'pool': [['BNB', 'ATD', 'ACC']]}
dff = pd.DataFrame(data)
dff.set_index('current_date', inplace=True)
dff.drop(dff.index, inplace=True)

command = 'node ./database/dl_for_quick_analysis.js'
path = "./database/quick_analysis"
ennDate = f"{ending_time} {hour}"
sttDate = f"{star_time} {hour}"
start_date = datetime.strptime(sttDate, "%Y-%m-%d %H:%M:%S")
end_date = datetime.strptime(ennDate, "%Y-%m-%d %H:%M:%S")

current_date = start_date

# Define the maximum number of threads
MAX_THREADS = 10

# Semaphore to control the concurrency
semaphore = threading.Semaphore(MAX_THREADS)

### Download all the OHLCV

In [9]:
def downloadingDate(current_date):
    # Acquire the semaphore
    semaphore.acquire()

    execute_terminal_command2(command, current_date.strftime("%Y-%m-%d"), hour)
    remove_non_csv_files(path)

    # Release the semaphore
    semaphore.release()

In [11]:
try:
    shutil.rmtree(path)
except:
    pass
threads = []
while current_date <= end_date:
    # thread = threading.Thread(target=downloadingDate, args=(current_date,))
    # thread.start()
    # threads.append(thread)
    downloadingDate(current_date)
    current_date += timedelta(days=1)

# Wait for all threads to finish
# for thread in threads:
#     thread.join()
print("Process is done!")

node ./database/dl_for_quick_analysis.js "2021-07-07" "00:00:00"

Loading 1/590 coins downloaded
Loading 2/590 coins downloaded
Loading 3/590 coins downloaded
Loading 4/590 coins downloaded
Loading 5/590 coins downloaded
Loading 6/590 coins downloaded
Loading 7/590 coins downloaded
Loading 8/590 coins downloaded
Loading 9/590 coins downloaded
Loading 10/590 coins downloaded
Loading 11/590 coins downloaded
Loading 12/590 coins downloaded
Loading 13/590 coins downloaded
Loading 14/590 coins downloaded
Loading 15/590 coins downloaded
Loading 16/590 coins downloaded
Loading 17/590 coins downloaded
Loading 18/590 coins downloaded
Loading 19/590 coins downloaded
Loading 20/590 coins downloaded
Loading 21/590 coins downloaded
Loading 22/590 coins downloaded
Loading 23/590 coins downloaded
Loading 24/590 coins downloaded
Loading 25/590 coins downloaded
Loading 26/590 coins downloaded
Loading 27/590 coins downloaded
Loading 28/590 coins downloaded
Loading 29/590 coins downloaded
Loading 30/590 

### Extraire all the pair names

In [5]:
pair_names = []

# Get the list of file names in the directory
file_names = os.listdir(path)

# Process each file name
for file_name in file_names:
    # Extract the pair name before the '$' character
    pair_name = file_name.split('$')[0]

    # Add the pair name to the list if it's not already present
    if pair_name not in pair_names:
        pair_names.append(pair_name)

# Print the list of unique pair names
print(pair_names)

['MTL-USDT:USDT', 'SPELL-USDT:USDT', 'XVG-USDT', 'BNX-USDT:USDT', 'OCEAN-USDT', 'BNB-USDT', 'FIS-USDT', '1000XEC-USDT:USDT', 'RIF-USDT', 'QNT-USDT', 'ETH-USDT:USDT', 'RUNE-USDT:USDT', 'CVC-USDT', 'VTHO-USDT', 'BUSD-USDT', 'API3-USDT', 'CELR-USDT', 'OGN-USDT', 'PROM-USDT', 'SSV-USDT', 'BLZ-USDT', 'ATA-USDT:USDT', 'VOXEL-USDT', 'VET-USDT:USDT', '1INCH-USDT:USDT', 'KSM-USDT', 'FLOW-USDT:USDT', 'IDEX-USDT:USDT', 'ERD-USDT', 'THETA-USDT:USDT', 'MINA-USDT', 'STG-USDT', 'TCT-USDT', 'CELO-USDT:USDT', 'AXS-USDT', 'GHST-USDT', 'GLM-USDT', 'XNO-USDT', 'AST-USDT', 'SNX-USDT', 'TLM-USDT', 'DGB-USDT:USDT', 'RARE-USDT', 'BEL-USDT:USDT', 'SNT-USDT', 'AION-USDT', '1000SHIB-USDT:USDT', 'NEBL-USDT', 'CHZ-USDT', 'GTO-USDT', 'DEGO-USDT', 'HC-USDT', 'MULTI-USDT', 'RGT-USDT', 'FIL-USDT', 'ETH-USDT', 'GAL-USDT', 'HBAR-USDT:USDT', 'BZRX-USDT', 'XEM-USDT', 'MCO-USDT', 'ALCX-USDT', 'ZEN-USDT:USDT', 'TOMO-USDT:USDT', 'ALPACA-USDT', 'LEND-USDT', 'RNDR-USDT:USDT', 'KDA-USDT', 'ERN-USDT', 'BTCST-USDT:USDT', 'ADA-USD

### Create the csv files for all the dates

In [6]:
pair_data = {}
# Process each file name
for file_name in file_names:
    # Extract the pair name before the '$' character
    pair_name = file_name.split('$')[0]

    # Check if the pair name is already in the dictionary
    if pair_name in pair_data:
        pair_data[pair_name].append(file_name)
    else:
        pair_data[pair_name] = [file_name]

# Iterate over the pair names and their corresponding files
for pair_name, files in pair_data.items():
    # Create a new file for the pair name
    output_file = os.path.join(path, f"{pair_name}.csv")

    # Open the output file in write mode
    with open(output_file, 'w', newline='') as csv_out:
        writer = csv.writer(csv_out)

        # Write the header to the output file
        writer.writerow(['date', 'open', 'high', 'low', 'close', 'volume'])

        # Iterate over the files for the pair name
        for file in files:
            # Open each input file
            with open(os.path.join(path, file), 'r') as csv_in:
                reader = csv.reader(csv_in)
                next(reader)  # Skip the header row

                # Write the data rows to the output file
                writer.writerows(reader)

    print(f"Created file: {output_file} with merged data and header.")

Created file: ./database/quick_analysis/MTL-USDT:USDT.csv with merged data and header.
Created file: ./database/quick_analysis/SPELL-USDT:USDT.csv with merged data and header.
Created file: ./database/quick_analysis/XVG-USDT.csv with merged data and header.
Created file: ./database/quick_analysis/BNX-USDT:USDT.csv with merged data and header.
Created file: ./database/quick_analysis/OCEAN-USDT.csv with merged data and header.
Created file: ./database/quick_analysis/BNB-USDT.csv with merged data and header.
Created file: ./database/quick_analysis/FIS-USDT.csv with merged data and header.
Created file: ./database/quick_analysis/1000XEC-USDT:USDT.csv with merged data and header.
Created file: ./database/quick_analysis/RIF-USDT.csv with merged data and header.
Created file: ./database/quick_analysis/QNT-USDT.csv with merged data and header.
Created file: ./database/quick_analysis/ETH-USDT:USDT.csv with merged data and header.
Created file: ./database/quick_analysis/RUNE-USDT:USDT.csv with m

### Remove rest of csv files

In [7]:
# Iterate over the file names
for file_name in file_names:
    # Check if the file name contains the '$' character
    if '$' in file_name:
        # Create the file path
        file_path = os.path.join(path, file_name)

        # Remove the file
        os.remove(file_path)
        print(f"Deleted file: {file_path}")

Deleted file: ./database/quick_analysis/MTL-USDT:USDT$2021-09-16.csv
Deleted file: ./database/quick_analysis/SPELL-USDT:USDT$2021-09-16.csv
Deleted file: ./database/quick_analysis/XVG-USDT$2021-07-29.csv
Deleted file: ./database/quick_analysis/BNX-USDT:USDT$2021-07-14.csv
Deleted file: ./database/quick_analysis/OCEAN-USDT$2021-11-15.csv
Deleted file: ./database/quick_analysis/BNB-USDT$2021-11-26.csv
Deleted file: ./database/quick_analysis/FIS-USDT$2021-07-23.csv
Deleted file: ./database/quick_analysis/1000XEC-USDT:USDT$2021-08-07.csv
Deleted file: ./database/quick_analysis/RIF-USDT$2021-08-21.csv
Deleted file: ./database/quick_analysis/QNT-USDT$2021-09-24.csv
Deleted file: ./database/quick_analysis/ETH-USDT:USDT$2021-11-27.csv
Deleted file: ./database/quick_analysis/RUNE-USDT:USDT$2021-07-09.csv
Deleted file: ./database/quick_analysis/CVC-USDT$2021-08-01.csv
Deleted file: ./database/quick_analysis/VTHO-USDT$2021-11-23.csv
Deleted file: ./database/quick_analysis/BUSD-USDT$2021-11-17.csv

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Deleted file: ./database/quick_analysis/MDX-USDT$2021-08-04.csv
Deleted file: ./database/quick_analysis/ZRX-USDT:USDT$2021-10-05.csv
Deleted file: ./database/quick_analysis/ENJ-USDT$2021-11-28.csv
Deleted file: ./database/quick_analysis/RUNE-USDT$2021-12-18.csv
Deleted file: ./database/quick_analysis/KLAY-USDT:USDT$2021-12-07.csv
Deleted file: ./database/quick_analysis/APE-USDT:USDT$2021-10-29.csv
Deleted file: ./database/quick_analysis/ACH-USDT:USDT$2021-11-29.csv
Deleted file: ./database/quick_analysis/TORN-USDT$2021-08-07.csv
Deleted file: ./database/quick_analysis/BAT-USDT:USDT$2021-12-01.csv
Deleted file: ./database/quick_analysis/LUNA2-USDT:USDT$2021-08-04.csv
Deleted file: ./database/quick_analysis/BZRX-USDT$2021-09-08.csv
Deleted file: ./database/quick_analysis/WBTC-USDT$2021-08-29.csv
Deleted file: ./database/quick_analysis/BETH-USDT$2021-12-31.csv
Deleted file: ./database/quick_analysis/AVA-USDT$2021-12-01.csv
Deleted file: ./database/quick_analysis/HIVE-USDT$2021-12-16.csv
D

### Remove redudancy in the csv files

In [8]:
# Get the list of file names in the directory
file_names = os.listdir(path)

# Iterate over the file names
for file_name in file_names:
    # Create the file path
    file_path = os.path.join(path, file_name)

    # Read the contents of the file
    with open(file_path, 'r') as file:
        lines = file.readlines()

    # Remove repeated rows and keep only the first occurrence
    unique_lines = []
    unique_set = set()
    for line in lines:
        if line not in unique_set:
            unique_lines.append(line)
            unique_set.add(line)

    # Write the unique lines back to the file
    with open(file_path, 'w') as file:
        file.writelines(unique_lines)

    print(f"Removed repeated rows from file: {file_path}")

Removed repeated rows from file: ./database/quick_analysis/USDC-USDT:USDT.csv
Removed repeated rows from file: ./database/quick_analysis/AUD-USDT.csv
Removed repeated rows from file: ./database/quick_analysis/PERL-USDT.csv
Removed repeated rows from file: ./database/quick_analysis/TCT-USDT.csv
Removed repeated rows from file: ./database/quick_analysis/AUCTION-USDT.csv
Removed repeated rows from file: ./database/quick_analysis/SUI-USDT:USDT.csv
Removed repeated rows from file: ./database/quick_analysis/AGIX-USDT:USDT.csv
Removed repeated rows from file: ./database/quick_analysis/BETA-USDT.csv
Removed repeated rows from file: ./database/quick_analysis/T-USDT:USDT.csv
Removed repeated rows from file: ./database/quick_analysis/THETA-USDT:USDT.csv
Removed repeated rows from file: ./database/quick_analysis/SPELL-USDT:USDT.csv
Removed repeated rows from file: ./database/quick_analysis/GLM-USDT.csv
Removed repeated rows from file: ./database/quick_analysis/ACM-USDT.csv
Removed repeated rows fr

# 2] Data Preprocessing

In [4]:
file_list = [f for f in listdir(path) if isfile(join(path, f))]
df_list = {}
for file in file_list:
    df_list[file[:-9]] = get_historical_from_path(path + "/" + file)
print("All data loaded")

All data loaded


In [5]:
# Convert the start and end times to datetime objects
start = datetime.strptime(star_time, "%Y-%m-%d")
end = datetime.strptime(ending_time, "%Y-%m-%d")
# Define the timedelta for incrementing the date
delta = timedelta(days=1)
# Loop through the dates between start and end
while start <= end:
    current_date = start.strftime("%Y-%m-%d")
    # Filter the dataframes to keep only the specific date
    filtered_dataframes = {}
    for key, df in df_list.items():
        filtered_df = df.loc[df.index.date == pd.to_datetime(start).date()]
        filtered_dataframes[key] = filtered_df
    df_metric = get_analyisis_from_window(filtered_dataframes,dateObservation).sort_values(by="volume_evolution", ascending=False)
    dfVe = df_metric.iloc[:nbPool]
    market = list(dfVe.index)
    dff.loc[datetime.strptime(current_date, "%Y-%m-%d")] = [list(dfVe['volume_evolution'].index)]
    start += delta

### Save the Pools By day dataframe

In [6]:
dff.to_csv('./database/pools.csv',header=False)

# 3] Generate All Combinations

In [7]:
crypto = {}
deltaHours = ["2h","4h","8h","12h"]
Ni = ["N","N-1","N-2"]
array1 = []
with open('database/pools.csv', 'r') as file:
    reader = csv.reader(file)
    for row in reader:
        timestamp = row[0]
        elements = row[1].strip('[]').split(', ')
        array1.append((timestamp, elements))
combinations = list(itertools.product(array1, deltaHours, Ni))
combinations = [list(item) for item in combinations]

# 4] Cocotier Process

In [8]:
def get_historical_klines(x,deltahour,sttDate,ennDate):
    # Open the CSV file
    file_path = f"./database/quick_analysis/{x}.csv"
    df = pd.read_csv(file_path)

    # Convert sttDate and ennDate to datetime objects
    stt_date = pd.to_datetime(sttDate, format="%Y-%m-%d %H:%M:%S")
    enn_date = pd.to_datetime(ennDate, format="%Y-%m-%d %H:%M:%S")

    # Convert the 'date' column to datetime
    df['date'] = pd.to_datetime(df['date'], unit='ms')

    # Filter the dataframe based on the start and end dates
    mask = (df['date'] >= stt_date) & (df['date'] <= enn_date)
    filtered_df = df.loc[mask]

    # Extract the delta hour value from the string (e.g., '2h', '4h')
    delta_hours = int(re.findall(r'\d+', deltahour)[0])

    # Create a time range at delta hour intervals
    time_range = pd.date_range(stt_date, enn_date, freq=f'{delta_hours}H')

    # Filter the dataframe to keep only the rows at delta hour intervals
    filtered_df = filtered_df[filtered_df['date'].isin(time_range)]

    # Create a new dataframe with the desired columns
    new_df = filtered_df[['date', 'open', 'close']].copy()
    new_df.columns = ['timestamp', f'{x.lower()}_open', f'{x.lower()}_close']

    return new_df

In [9]:
def cocotier(combination):
    semaphore.acquire()
    crypto = {}
    x = ""
    for elm in combination[0][1] :
        try :
            x = elm.replace("'","")
            try :
                crypto[x] = get_historical_klines(x,combination[1],sttDate,ennDate)
            except :
                crypto[x] = get_historical_klines(x+"-UDST",combination[1],sttDate,ennDate)
            crypto[x] = crypto[x].astype({x.lower()+ '_open': 'float64',x.lower()+ '_close': 'float64'})
            crypto[x] = crypto[x].set_index('timestamp')
        except Exception as ll:
            print(f"{ll}\n{x}!")
            traceback.format_exc()
    try :
        array_mauvais_shape = detection_mauvais_shape(crypto)
        # crypto = correction_shape(crypto, array_mauvais_shape)
        # for elm in array_mauvais_shape:
        #     crypto[elm]['timestamp'] = generation_date(crypto[elm], int(delta_hour[:1]))
        #     crypto[elm] = crypto[elm].set_index('timestamp')
        for i in array_mauvais_shape:
            del crypto[i]
        crypto = variationN(crypto, combination[2])
        crypto = coeffMulti(crypto)
        crypto = mergeCryptoTogether(crypto)
        crypto, maxis = botMax(crypto)
        crypto = botMaxVariation2(crypto, maxis)
        crypto = coeffMultiBotMax(crypto)
        coefMulti = coefmultiFinal(crypto)
        combination.append(coefMulti.tail(1).iloc[-1,-1])
    except Exception as ll:
        print(f"{ll}\n")
    semaphore.release()

In [10]:
# Launch a thread for each iteration
threads = []
combinations = list(combinations)
for combination in combinations:
    thread = threading.Thread(target=cocotier, args=(combination,))
    thread.start()
    threads.append(thread)

# Wait for all threads to finish
for thread in threads:
    thread.join()

[Errno 2] No such file or directory: './database/quick_analysis/AUD.csv'
AUD!
[Errno 2] No such file or directory: './database/quick_analysis/AUD.csv'
AUD!
[Errno 2] No such file or directory: './database/quick_analysis/AUD.csv'
AUD!
[Errno 2] No such file or directory: './database/quick_analysis/AUD.csv'
AUD!
[Errno 2] No such file or directory: './database/quick_analysis/AUD.csv'
AUD!
[Errno 2] No such file or directory: './database/quick_analysis/AUD.csv'
AUD!
[Errno 2] No such file or directory: './database/quick_analysis/AUD.csv'
AUD!
[Errno 2] No such file or directory: './database/quick_analysis/AUD.csv'
AUD!
[Errno 2] No such file or directory: './database/quick_analysis/AUD.csv'
AUD!
[Errno 2] No such file or directory: './database/quick_analysis/AUD.csv'
AUD!
[Errno 2] No such file or directory: './database/quick_analysis/CTK.csv'
CTK!
[Errno 2] No such file or directory: './database/quick_analysis/CTK.csv'
CTK!
[Errno 2] No such file or directory: './database/quick_analysis/

# 5] Presenting the First DataFrame

In [11]:
# Flatten the nested lists
flat_data = []
for combination in combinations:
    datetime = combination[0][0]
    pool = combination[0][1]
    deltahour = combination[1]
    Ni = combination[2]
    BotMax = combination[3]
    flat_data.append([datetime, deltahour, Ni, BotMax, pool])
df = pd.DataFrame(flat_data, columns=['datetime', 'deltahour', 'Ni', 'BotMax','pool'])

# 6] Produit Cumulée and final Dataframe

In [12]:
# Convert 'datetime' column to datetime format
df['datetime'] = pd.to_datetime(df['datetime'])

# Group DataFrame by 'deltahour' and 'Ni', calculate product of 'BotMax'
df_grouped = df.groupby(['deltahour', 'Ni']).agg({'datetime': ['min', 'max'], 'BotMax': 'prod'}).reset_index()

# Rename columns
df_grouped.columns = ['deltahour', 'Ni', 'startDate', 'endingDate', 'BotMax']

# Convert 'startDate' and 'endingDate' columns to desired format
df_grouped['startDate'] = df_grouped['startDate'].dt.strftime('%Y-%m-%d %H:%M:%S')
df_grouped['endingDate'] = df_grouped['endingDate'].dt.strftime('%Y-%m-%d %H:%M:%S')


In [13]:
print(df_grouped)

   deltahour   Ni            startDate           endingDate        BotMax
0        12h    N  2021-07-07 00:00:00  2022-01-01 00:00:00  3.891965e-02
1        12h  N-1  2021-07-07 00:00:00  2022-01-01 00:00:00  3.891965e-02
2        12h  N-2  2021-07-07 00:00:00  2022-01-01 00:00:00  3.891965e-02
3         2h    N  2021-07-07 00:00:00  2022-01-01 00:00:00  3.547013e-04
4         2h  N-1  2021-07-07 00:00:00  2022-01-01 00:00:00  3.547013e-04
5         2h  N-2  2021-07-07 00:00:00  2022-01-01 00:00:00  3.547013e-04
6         4h    N  2021-07-07 00:00:00  2022-01-01 00:00:00  1.351247e+10
7         4h  N-1  2021-07-07 00:00:00  2022-01-01 00:00:00  1.351247e+10
8         4h  N-2  2021-07-07 00:00:00  2022-01-01 00:00:00  1.351247e+10
9         8h    N  2021-07-07 00:00:00  2022-01-01 00:00:00  1.868115e+02
10        8h  N-1  2021-07-07 00:00:00  2022-01-01 00:00:00  1.868115e+02
11        8h  N-2  2021-07-07 00:00:00  2022-01-01 00:00:00  1.868115e+02
